In [86]:
import lzma
import sys
from io import StringIO
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
import numpy

pathX = "./train/train.tsv.xz"
# pathX = "./train/in.tsv"
# pathY = "./train/meta.tsv.xz"
nrows = 100000

In [87]:
# data = lzma.open(pathX, mode='rt', encoding='utf-8').read()
# stringIO = StringIO(data)
# df = pd.read_csv(stringIO, sep="\t", header=None)
df = pd.read_csv(pathX, sep='\t', nrows=nrows, header=None)
# df = df.drop(df.columns, axis=1)
# topics = pd.read_csv(pathY, sep='\t', nrows=nrows, header=None)

In [88]:
print(len(df.index))

# print(len(topics.index))


100000


In [66]:
def mergeTexts(a, b, c):
    return str(a) + " " + str(b) + " " + str(c)

In [67]:
def getMean(a, b):
    return ((a + b)/2)

In [89]:
df["year"] = df.apply(lambda x: getMean(x[0], x[1]), axis = 1)
df["text"] = df.apply(lambda x: x[4], axis = 1)

In [90]:
df = df.drop(columns = [0,1,2,3,4], axis=1)
df.sample(5)

year                                               text
63552  2013.212329  dnia 10 października 2012r., znak (...)/, Zakł...
89500  2013.656164  postępowania, skarżąca wniosła, jak na wstępie...
94039  1925.015068  dzieją się ciągle awantury, nieustają podejrze...
62566  2012.348361  Samodzielnego Publicznego Zespołu Opieki Zdrow...
87553  1975.494521  doprowadzających przeładowywane produkty od st...

In [91]:
topics = df.pop('year')
df.sample(5)

text
85466  pokoJenie dOInu Burbonów, zaprzestalo we Frano...
416    non. Jakiekolwiek próby odbudowy takich instyt...
36354  000 ludzi, a który był iście tryumf.ilnym. trw...
95566  do robienia lodów. Ogrodzenia do kląbów w wiel...
58632  ftcitnciu>a4ii. Dzień już dal nogę i mrugali g...

In [92]:
topics.sample(5)

22843    1991.500000
12830    1937.157534
63119    1919.500000
77638    2010.130137
5577     1934.768493
Name: year, dtype: float64

In [93]:
vectorizer = TfidfVectorizer(lowercase=True, stop_words=['polish'])
X = vectorizer.fit_transform(df.to_numpy().ravel())
vectorizer.get_feature_names_out()


array(['00', '000', '0000', ..., 'תורהט', 'תותיירב', 'תשדוקמ'],
      dtype=object)

In [73]:
# vectorizer.transform("Ala ma kotka".lower().split())

In [74]:
# df = df.reset_index()

In [94]:
tfidfVector = vectorizer.transform(df["text"])

    

In [76]:
# from sklearn.model_selection import train_test_split
# from sklearn.naive_bayes import GaussianNB
# 
# gnb = GaussianNB()
# gnb.fit(tfidfVector.todense(), topics)

In [95]:
from sklearn.linear_model import LinearRegression

reg = LinearRegression().fit(tfidfVector, topics)


In [106]:
testXPath = "./dev-0/in.tsv"
testYPath = "./dev-0/expected.tsv"

testX = pd.read_csv(testXPath, sep='\t', nrows=19998, header=None)

testY = pd.read_csv(testYPath, sep='\t', nrows=19998, header=None)


In [107]:
testX.sample(5)

0
9194   że w moich oczach umizgasz się do niej. Rzeczy...
3959   reką dopoty, dopóki nic wyiaanię !Prawiü Bye m...
19210  końcach klapy wentylacyjnej i zapobiegają odch...
6080   lat cię- owe g\\\\ allowne walki w dziennikars...
18845  elektr,yczne] ny, poszanowania ładu i po- roc1...

In [108]:
testY.sample()


0
3849  1956.476776

In [109]:
testXtfidfVector = vectorizer.transform(testX[0])


In [110]:
reg.score(testXtfidfVector, testY[0])


-0.3101240322770993

In [157]:
testXPath = "./test-A/in.tsv"
testYPath = "./test-A/out.tsv"

# testX = pd.read_csv(testXPath, sep='\t', nrows=nrows, header=None, skip_blank_lines=False)
# testY = pd.read_csv(testYPath, sep='\t', nrows=nrows, header=None)
reviews = []
with open(testXPath, 'r', encoding="utf8") as openfile:
    for line in openfile:
        reviews.append(line)
    testX = pd.DataFrame(reviews)
testXtfidfVector = vectorizer.transform(testX[0])


In [158]:
print(testX.shape[0])

print(testXtfidfVector.shape[0])

14220
14220


In [159]:
pred = reg.predict(testXtfidfVector)
print(len(pred))

import csv
with open(testYPath, 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\n')
    tsv_output.writerow(pred)

14220
